# Neighbourhoods of New York and Toronto

#### Finding best city from two cities(New york or Toronto) to open new diffent type of stores like pizza,restaurents,coffee shops etc.

In [1]:
from bs4 import BeautifulSoup
import requests
import pandas as pd

In [2]:
page= requests.get("https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M").text

toronto_list = pd.read_html(page, header=0, attrs={"class":"wikitable sortable"})[0]
toronto_list.head()

Postcode           Borough     Neighbourhood
0      M1A      Not assigned      Not assigned
1      M2A      Not assigned      Not assigned
2      M3A        North York         Parkwoods
3      M4A        North York  Victoria Village
4      M5A  Downtown Toronto      Harbourfront

In [3]:
toronto_df=pd.DataFrame(toronto_list)

In [4]:
toronto_df.columns

Index(['Postcode', 'Borough', 'Neighbourhood'], dtype='object')

In [5]:
toronto_df.shape

(289, 3)

### Preprocessing the Newyork Data

In [6]:
toronto_df.head()

Postcode           Borough     Neighbourhood
0      M1A      Not assigned      Not assigned
1      M2A      Not assigned      Not assigned
2      M3A        North York         Parkwoods
3      M4A        North York  Victoria Village
4      M5A  Downtown Toronto      Harbourfront

In [7]:
borough_indexes=toronto_df[toronto_df['Borough']=='Not assigned'].index
borough_indexes

Int64Index([  0,   1,   9,  13,  20,  21,  30,  36,  37,  45,  46,  50,  51,
             52,  54,  55,  59,  60,  61,  73,  74,  75,  88,  89,  90, 104,
            105, 106, 120, 121, 136, 137, 148, 149, 155, 161, 162, 167, 175,
            181, 182, 188, 189, 190, 194, 195, 201, 202, 203, 204, 209, 210,
            223, 224, 238, 239, 242, 243, 248, 249, 254, 255, 259, 260, 261,
            262, 264, 265, 275, 276, 277, 278, 279, 280, 281, 282, 288],
           dtype='int64')

In [8]:
toronto_df.drop(toronto_df.index[borough_indexes],inplace=True)

In [9]:
toronto_df.head()

Postcode           Borough     Neighbourhood
2      M3A        North York         Parkwoods
3      M4A        North York  Victoria Village
4      M5A  Downtown Toronto      Harbourfront
5      M5A  Downtown Toronto       Regent Park
6      M6A        North York  Lawrence Heights

In [10]:
neighbour_indexes=toronto_df[toronto_df['Neighbourhood']=='Not assigned'].index
neighbour_indexes

Int64Index([8], dtype='int64')

In [11]:
toronto_df.drop(toronto_df.index[neighbour_indexes],inplace=True)

In [12]:
toronto_df.head()

Postcode           Borough     Neighbourhood
2      M3A        North York         Parkwoods
3      M4A        North York  Victoria Village
4      M5A  Downtown Toronto      Harbourfront
5      M5A  Downtown Toronto       Regent Park
6      M6A        North York  Lawrence Heights

#### Merging the Toronto cities into one row

In [13]:
toronto_data=toronto_df.groupby(['Postcode','Borough'])['Neighbourhood'].apply(','.join).reset_index()

In [14]:
toronto_data.head()

Postcode      Borough                         Neighbourhood
0      M1B  Scarborough                               Malvern
1      M1C  Scarborough  Highland Creek,Rouge Hill,Port Union
2      M1E  Scarborough       Guildwood,Morningside,West Hill
3      M1G  Scarborough                                Woburn
4      M1H  Scarborough                             Cedarbrae

In [15]:
print('The dataframe has {} boroughs and {} neighborhoods.'.format(
        len(toronto_data['Borough'].unique()),
        toronto_data.shape[0]
    )
)

The dataframe has 11 boroughs and 103 neighborhoods.


### Now we have to set Latitude and Longitude of Toronto

In [16]:
geo_data_df = pd.read_csv('https://cocl.us/Geospatial_data')
geo_data_df.head()

Postal Code   Latitude  Longitude
0         M1B  43.806686 -79.194353
1         M1C  43.784535 -79.160497
2         M1E  43.763573 -79.188711
3         M1G  43.770992 -79.216917
4         M1H  43.773136 -79.239476

In [17]:
geo_data_df.columns

Index(['Postal Code', 'Latitude', 'Longitude'], dtype='object')

In [18]:
merged_toronto_data=pd.merge(toronto_data,geo_data_df,left_on='Postcode',right_on='Postal Code',how='left').drop('Postal Code',axis=1)
merged_toronto_data.head()

Postcode      Borough                         Neighbourhood   Latitude  \
0      M1B  Scarborough                               Malvern  43.806686   
1      M1C  Scarborough  Highland Creek,Rouge Hill,Port Union  43.784535   
2      M1E  Scarborough       Guildwood,Morningside,West Hill  43.763573   
3      M1G  Scarborough                                Woburn  43.770992   
4      M1H  Scarborough                             Cedarbrae  43.773136   

   Longitude  
0 -79.194353  
1 -79.160497  
2 -79.188711  
3 -79.216917  
4 -79.239476

In [19]:
tor_data=merged_toronto_data.drop(['Postcode'],axis=1)
tor_data.head()

Borough                         Neighbourhood   Latitude  Longitude
0  Scarborough                               Malvern  43.806686 -79.194353
1  Scarborough  Highland Creek,Rouge Hill,Port Union  43.784535 -79.160497
2  Scarborough       Guildwood,Morningside,West Hill  43.763573 -79.188711
3  Scarborough                                Woburn  43.770992 -79.216917
4  Scarborough                             Cedarbrae  43.773136 -79.239476

In [20]:
tor_data.shape

(103, 4)

## Now we have to Import New York Data

In [21]:
!wget -q -O 'newyork_data.json' https://ibm.box.com/shared/static/fbpwbovar7lf8p5sgddm06cgipa2rxpe.json
print('Data downloaded!')

Data downloaded!


In [22]:
import json # library to handle JSON files

In [23]:
with open('newyork_data.json') as json_data:
    newyork_data=json.load(json_data)

In [24]:
neighbourhoods_data=newyork_data['features']
neighbourhoods_data[0]

{'geometry': {'coordinates': [-73.84720052054902, 40.89470517661],
  'type': 'Point'},
 'geometry_name': 'geom',
 'id': 'nyu_2451_34572.1',
 'properties': {'annoangle': 0.0,
  'annoline1': 'Wakefield',
  'annoline2': None,
  'annoline3': None,
  'bbox': [-73.84720052054902,
   40.89470517661,
   -73.84720052054902,
   40.89470517661],
  'borough': 'Bronx',
  'name': 'Wakefield',
  'stacked': 1},
 'type': 'Feature'}

In [25]:
Coloumn_names=['Borough','Neighbourhood','Latitude','Longitude']
newyorkdata=pd.DataFrame(columns=Coloumn_names)

In [26]:
for data in neighbourhoods_data:
    borough = neighborhood_name = data['properties']['borough'] 
    neighborhood_name = data['properties']['name']
        
    neighborhood_latlon = data['geometry']['coordinates']
    neighborhood_lat = neighborhood_latlon[1]
    neighborhood_lon = neighborhood_latlon[0]
    
    newyorkdata = newyorkdata.append({'Borough': borough,
                                          'Neighbourhood': neighborhood_name,
                                          'Latitude': neighborhood_lat,
                                          'Longitude': neighborhood_lon}, ignore_index=True)

In [27]:
print('The dataframe has {} boroughs and {} neighbourhoods.'.format(
        len(newyorkdata['Borough'].unique()),
        newyorkdata.shape[0]
    )
)

The dataframe has 5 boroughs and 306 neighbourhoods.


In [28]:
newyorkdata=newyorkdata.drop_duplicates(['Neighbourhood'])

In [29]:
print(newyorkdata.shape)
newyorkdata.head()

(302, 4)


Borough Neighbourhood   Latitude  Longitude
0   Bronx     Wakefield  40.894705 -73.847201
1   Bronx    Co-op City  40.874294 -73.829939
2   Bronx   Eastchester  40.887556 -73.827806
3   Bronx     Fieldston  40.895437 -73.905643
4   Bronx     Riverdale  40.890834 -73.912585

We have 306 neighborhoods and 5 boroughs in Newyork Data <br>
and 103 neighborhoods and 11 boroughs in Toronto Data 

### Now we have to findout the different venues in two Cities (Newyork and Toronto)

Installing Geographic library for finding location 

In [30]:
!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

Fetching package metadata .............
Solving package specifications: .

# All requested packages already installed.
# packages in environment at /opt/conda/envs/DSX-Python35:
#
geopy                     1.18.1                     py_0    conda-forge


Creating Map for Newyork Neighborhoods

In [31]:
address = 'New York City, NY'

geolocator = Nominatim()
location = geolocator.geocode(address)
newyork_latitude = location.latitude
newyork_longitude = location.longitude
print('The geograpical coordinate of New York City are {}, {}.'.format(newyork_latitude, newyork_longitude))

/opt/conda/envs/DSX-Python35/lib/python3.5/site-packages/ipykernel/__main__.py:3: DeprecationWarning: Using Nominatim with the default "geopy/1.18.1" `user_agent` is strongly discouraged, as it violates Nominatim's ToS https://operations.osmfoundation.org/policies/nominatim/ and may possibly cause 403 and 429 HTTP errors. Please specify a custom `user_agent` with `Nominatim(user_agent="my-application")` or by overriding the default `user_agent`: `geopy.geocoders.options.default_user_agent = "my-application"`. In geopy 2.0 this will become an exception.
  app.launch_new_instance()


The geograpical coordinate of New York City are 40.7308619, -73.9871558.


In [32]:
!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library

Fetching package metadata .............
Solving package specifications: .

# All requested packages already installed.
# packages in environment at /opt/conda/envs/DSX-Python35:
#
folium                    0.5.0                      py_0    conda-forge


In [33]:
# create map of New York using latitude and longitude values
map_newyork = folium.Map(location=[newyork_latitude, newyork_longitude], zoom_start=10)

# add markers to map
for lat, lng, borough, neighbourhood in zip(newyorkdata['Latitude'], newyorkdata['Longitude'], newyorkdata['Borough'], newyorkdata['Neighbourhood']):
    label = '{}, {}'.format(neighbourhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_newyork)  
    
map_newyork

## Creating Map for Toronto Neighbourhoods

In [34]:
address = 'Toronto, T'

geolocator = Nominatim()
location = geolocator.geocode(address)
toronto_latitude = location.latitude
toronto_longitude = location.longitude
print('The geograpical coordinate of Toronto City are {}, {}.'.format(toronto_latitude, toronto_longitude))

/opt/conda/envs/DSX-Python35/lib/python3.5/site-packages/ipykernel/__main__.py:3: DeprecationWarning: Using Nominatim with the default "geopy/1.18.1" `user_agent` is strongly discouraged, as it violates Nominatim's ToS https://operations.osmfoundation.org/policies/nominatim/ and may possibly cause 403 and 429 HTTP errors. Please specify a custom `user_agent` with `Nominatim(user_agent="my-application")` or by overriding the default `user_agent`: `geopy.geocoders.options.default_user_agent = "my-application"`. In geopy 2.0 this will become an exception.
  app.launch_new_instance()


The geograpical coordinate of Toronto City are 43.653963, -79.387207.


In [35]:
# create map of New York using latitude and longitude values
map_toronto = folium.Map(location=[toronto_latitude, toronto_longitude], zoom_start=10)

# add markers to map
for lat, lng, borough, neighbourhood in zip(tor_data['Latitude'], tor_data['Longitude'], tor_data['Borough'], tor_data['Neighbourhood']):
    label = '{}, {}'.format(neighbourhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_toronto)  
    
map_toronto

## Creating Foursquare Url for New York to find the locations

In [80]:
CLIENT_ID = 'V4R2D1ZL5GMRDPXDVRCXRNEP5UFBXMP1WTNBI2RLNAQPPTGD' # your Foursquare ID
CLIENT_SECRET = 'O1BSCSZSQSYFY5WKSTOWCDDJRMV3EXEATF50DRCAGYZ0Y0XV' # your Foursquare Secret
VERSION = '20190112' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: V4R2D1ZL5GMRDPXDVRCXRNEP5UFBXMP1WTNBI2RLNAQPPTGD
CLIENT_SECRET:O1BSCSZSQSYFY5WKSTOWCDDJRMV3EXEATF50DRCAGYZ0Y0XV


In [81]:
LIMIT = 100
radius = 500
url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
    CLIENT_ID, 
    CLIENT_SECRET, 
    VERSION, 
    newyork_latitude, 
    newyork_longitude, 
    radius, 
    LIMIT)
url # display URL

'https://api.foursquare.com/v2/venues/explore?&client_id=V4R2D1ZL5GMRDPXDVRCXRNEP5UFBXMP1WTNBI2RLNAQPPTGD&client_secret=O1BSCSZSQSYFY5WKSTOWCDDJRMV3EXEATF50DRCAGYZ0Y0XV&v=20190112&ll=40.7308619,-73.9871558&radius=500&limit=100'

Send the GET request and examine the resutls

In [82]:
newyork_results = requests.get(url).json()
newyork_results

{'meta': {'code': 200, 'requestId': '5c3a9336f594df0eaee2bc2a'},
 'response': {'groups': [{'items': [{'reasons': {'count': 0,
       'items': [{'reasonName': 'globalInteractionReason',
         'summary': 'This spot is popular',
         'type': 'general'}]},
      'referralId': 'e-0-3fd66200f964a5203de41ee3-0',
      'venue': {'categories': [{'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/nightlife/sake_',
          'suffix': '.png'},
         'id': '4bf58dd8d48988d11c941735',
         'name': 'Sake Bar',
         'pluralName': 'Sake Bars',
         'primary': True,
         'shortName': 'Sake Bar'}],
       'id': '3fd66200f964a5203de41ee3',
       'location': {'address': '240 E 9th St',
        'cc': 'US',
        'city': 'New York',
        'country': 'United States',
        'crossStreet': 'btwn 2nd & 3rd Ave.',
        'distance': 168,
        'formattedAddress': ['240 E 9th St (btwn 2nd & 3rd Ave.)',
         'New York, NY 10003',
         'United States'],
        'l

### Writing the function to extracts the category of the venue

In [83]:
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

#### cleaning the json and structure it into a *pandas* dataframe.

In [84]:
import requests 
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)
import json # library to handle JSON files
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

In [85]:
venues = newyork_results['response']['groups'][0]['items']
    
nearby_venues = json_normalize(venues) # flatten JSON

# filter columns
filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng']
nearby_venues =nearby_venues.loc[:, filtered_columns]

# filter the category for each row
nearby_venues['venue.categories'] = nearby_venues.apply(get_category_type, axis=1)

# clean columns
nearby_venues.columns = [col.split(".")[-1] for col in nearby_venues.columns]

nearby_venues.head()

name           categories        lat        lng
0              Sake Bar Decibel             Sake Bar  40.729418 -73.987769
1             Momofuku Ssäm Bar     Asian Restaurant  40.731718 -73.985554
2                   Han Dynasty   Chinese Restaurant  40.732130 -73.988090
3  Hi-Collar - ハイカラ (Hi-Collar)          Coffee Shop  40.729449 -73.985918
4            Casey Rubber Stamp  Arts & Crafts Store  40.729962 -73.985098

In [86]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighbourhood', 
                  'Neighbourhood Latitude', 
                  'Neighbourhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [87]:
newyork_venues = getNearbyVenues(names=newyorkdata['Neighbourhood'],
                                   latitudes=newyorkdata['Latitude'],
                                   longitudes=newyorkdata['Longitude']
                                  )


Wakefield
Co-op City
Eastchester
Fieldston
Riverdale
Kingsbridge
Marble Hill
Woodlawn
Norwood
Williamsbridge
Baychester
Pelham Parkway
City Island
Bedford Park
University Heights
Morris Heights
Fordham
East Tremont
West Farms
High  Bridge
Melrose
Mott Haven
Port Morris
Longwood
Hunts Point
Morrisania
Soundview
Clason Point
Throgs Neck
Country Club
Parkchester
Westchester Square
Van Nest
Morris Park
Belmont
Spuyten Duyvil
North Riverdale
Pelham Bay
Schuylerville
Edgewater Park
Castle Hill
Olinville
Pelham Gardens
Concourse
Unionport
Edenwald
Bay Ridge
Bensonhurst
Sunset Park
Greenpoint
Gravesend
Brighton Beach
Sheepshead Bay
Manhattan Terrace
Flatbush
Crown Heights
East Flatbush
Kensington
Windsor Terrace
Prospect Heights
Brownsville
Williamsburg
Bushwick
Bedford Stuyvesant
Brooklyn Heights
Cobble Hill
Carroll Gardens
Red Hook
Gowanus
Fort Greene
Park Slope
Cypress Hills
East New York
Starrett City
Canarsie
Flatlands
Mill Island
Manhattan Beach
Coney Island
Bath Beach
Borough Park
Dyker

In [88]:
newyork_venues.head()

Neighbourhood  Neighbourhood Latitude  Neighbourhood Longitude  \
0     Wakefield               40.894705               -73.847201   
1     Wakefield               40.894705               -73.847201   
2     Wakefield               40.894705               -73.847201   
3     Wakefield               40.894705               -73.847201   
4     Wakefield               40.894705               -73.847201   

              Venue  Venue Latitude  Venue Longitude  Venue Category  
0  Lollipops Gelato       40.894123       -73.845892    Dessert Shop  
1          Rite Aid       40.896521       -73.844680        Pharmacy  
2  Carvel Ice Cream       40.890487       -73.848568  Ice Cream Shop  
3     Dunkin Donuts       40.890631       -73.849027      Donut Shop  
4            SUBWAY       40.890656       -73.849192  Sandwich Place

In [89]:
newyork_venues.shape

(10183, 7)

In [90]:
newyork_venues.groupby('Neighbourhood').count()

Neighbourhood Latitude  Neighbourhood Longitude  \
Neighbourhood                                                                
Allerton                                       32                       32   
Annadale                                        9                        9   
Arden Heights                                   5                        5   
Arlington                                       8                        8   
Arrochar                                       20                       20   
Arverne                                        15                       15   
Astoria                                       100                      100   
Astoria Heights                                14                       14   
Auburndale                                     21                       21   
Bath Beach                                     54                       54   
Battery Park City                             100                      100   
Bay Ridge                                      87                       87   
Bay Terrace                                    40                       40   
Baychester                                     19                       19   
Bayside                                        72                       72   
Bayswater                                       3                        3   
Bedford Park                                   39                       39   
Bedford Stuyvesant                             27                       27   
Beechhurst                                     16                       16   
Bellaire                                       15                       15   
Belle Harbor                                   17                       17   
Bellerose                                      21                       21   
Belmont                                        99                       99   
Bensonhurst                                    31                       31   
Bergen Beach                                    8                        8   
Blissville                                     21                       21   
Bloomfield                                      4                        4   
Boerum Hill                                    84                       84   
Borough Park                                   20                       20   
Breezy Point                                    7                        7   
Briarwood                                      12                       12   
Brighton Beach                                 43                       43   
Broad Channel                                   4                        4   
Broadway Junction                              16                       16   
Bronxdale                                      15                       15   
Brooklyn Heights                              100                      100   
Brookville                                      3                        3   
Brownsville                                    18                       18   
Bulls Head                                     43                       43   
Bushwick                                       72                       72   
Butler Manor                                    6                        6   
Cambria Heights                                13                       13   
Canarsie                                        6                        6   
Carnegie Hill                                 100                      100   
Carroll Gardens                               100                      100   
Castle Hill                                    10                       10   
Castleton Corners                              16                       16   
Central Harlem                                 43                       43   
Charleston                                     31                       31   
Chelsea                                       100

### Finding the Unique Categories 

In [91]:
len(newyork_venues['Venue Category'].unique())

429

In [92]:
# one hot encoding
newyork_onehot = pd.get_dummies(newyork_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
newyork_onehot['Neighbourhood'] = newyork_venues['Neighbourhood'] 

# move neighborhood column to the first column
fixed_columns = [newyork_onehot.columns[-1]] + list(newyork_onehot.columns[:-1])
newyork_onehot = newyork_onehot[fixed_columns]

newyork_onehot.head()

Neighbourhood  Accessories Store  Adult Boutique  Afghan Restaurant  \
0     Wakefield                  0               0                  0   
1     Wakefield                  0               0                  0   
2     Wakefield                  0               0                  0   
3     Wakefield                  0               0                  0   
4     Wakefield                  0               0                  0   

   African Restaurant  Airport Terminal  Airport Tram  American Restaurant  \
0                   0                 0             0                    0   
1                   0                 0             0                    0   
2                   0                 0             0                    0   
3                   0                 0             0                    0   
4                   0                 0             0                    0   

   Animal Shelter  Antique Shop  Arcade  Arepa Restaurant  \
0               0             0       0                 0   
1               0             0       0                 0   
2               0             0       0                 0   
3               0             0       0                 0   
4               0             0       0                 0   

   Argentinian Restaurant  Art Gallery  Art Museum  Arts & Crafts Store  \
0                       0            0           0                    0   
1                       0            0           0                    0   
2                       0            0           0                    0   
3                       0            0           0                    0   
4                       0            0           0                    0   

   Arts & Entertainment  Asian Restaurant  Athletics & Sports  Auditorium  \
0                     0                 0                   0           0   
1                     0                 0                   0           0   
2                     0                 0                   0           0   
3                     0                 0                   0           0   
4                     0                 0                   0           0   

   Australian Restaurant  Austrian Restaurant  Auto Workshop  Automotive Shop  \
0                      0                    0              0                0   
1                      0                    0              0                0   
2                      0                    0              0                0   
3                      0                    0              0                0   
4                      0                    0              0                0   

   BBQ Joint  Baby Store  Bagel Shop  Bakery  Bank  Bar  Baseball Field  \
0          0           0           0       0     0    0               0   
1          0           0           0       0     0    0               0   
2          0           0           0       0     0    0               0   
3          0           0           0       0     0    0               0   
4          0           0           0       0     0    0               0   

   Baseball Stadium  Basketball Court  Beach  Beach Bar  Bed & Breakfast  \
0                 0                 0      0          0                0   
1                 0                 0      0          0                0   
2                 0                 0      0          0                0   
3                 0                 0      0          0                0   
4                 0                 0      0          0                0   

   Beer Bar  Beer Garden  Beer Store  Belgian Restaurant  Big Box Store  \
0         0            0           0                   0              0   
1         0            0           0                   0              0   
2         0            0           0                   0              0   
3         0            0           0                   0              0   
4         0            0           0       

In [93]:
newyork_grouped = newyork_onehot.groupby('Neighbourhood').mean().reset_index()
newyork_grouped

Neighbourhood  Accessories Store  Adult Boutique  \
0                     Allerton           0.000000            0.00   
1                     Annadale           0.000000            0.00   
2                Arden Heights           0.000000            0.00   
3                    Arlington           0.000000            0.00   
4                     Arrochar           0.000000            0.00   
5                      Arverne           0.000000            0.00   
6                      Astoria           0.000000            0.00   
7              Astoria Heights           0.000000            0.00   
8                   Auburndale           0.000000            0.00   
9                   Bath Beach           0.000000            0.00   
10           Battery Park City           0.000000            0.00   
11                   Bay Ridge           0.000000            0.00   
12                 Bay Terrace           0.025000            0.00   
13                  Baychester           0.000000            0.00   
14                     Bayside           0.000000            0.00   
15                   Bayswater           0.000000            0.00   
16                Bedford Park           0.000000            0.00   
17          Bedford Stuyvesant           0.000000            0.00   
18                  Beechhurst           0.000000            0.00   
19                    Bellaire           0.000000            0.00   
20                Belle Harbor           0.000000            0.00   
21                   Bellerose           0.000000            0.00   
22                     Belmont           0.000000            0.00   
23                 Bensonhurst           0.000000            0.00   
24                Bergen Beach           0.000000            0.00   
25                  Blissville           0.000000            0.00   
26                  Bloomfield           0.000000            0.00   
27                 Boerum Hill           0.000000            0.00   
28                Borough Park           0.000000            0.00   
29                Breezy Point           0.000000            0.00   
30                   Briarwood           0.000000            0.00   
31              Brighton Beach           0.000000            0.00   
32               Broad Channel           0.000000            0.00   
33           Broadway Junction           0.000000            0.00   
34                   Bronxdale           0.000000            0.00   
35            Brooklyn Heights           0.000000            0.00   
36                  Brookville           0.000000            0.00   
37                 Brownsville           0.000000            0.00   
38                  Bulls Head           0.000000            0.00   
39                    Bushwick           0.000000            0.00   
40                Butler Manor           0.000000            0.00   
41             Cambria Heights           0.000000            0.00   
42                    Canarsie           0.000000            0.00   
43               Carnegie Hill           0.000000            0.00   
44             Carroll Gardens           0.000000            0.00   
45                 Castle Hill           0.000000            0.00   
46           Castleton Corners           0.000000            0.00   
47              Central Harlem           0.000000            0.00   
48                  Charleston           0.000000            0.00   
49                     Chelsea           0.000000            0.00   
50                   Chinatown           0.000000            0.00   
51                 City Island           0.000000            0.00   
52                   City Line           0.000000            0.00   
53                Civic Center           0.000000            0.00   
54           Claremont Village           0.000000            0.00   
55                Clason Point           0.000000            0.00   
56                     Clifton           0.000000            0.00   
57             

### Finding the Frequency of Neighbourhoods for New York

In [94]:
num_top_venues = 5

for hood in newyork_grouped['Neighbourhood']:
    print("----"+hood+"----")
    temp = newyork_grouped[newyork_grouped['Neighbourhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=True).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Allerton----
                   venue  freq
0      Accessories Store   0.0
1     Persian Restaurant   0.0
2  Performing Arts Venue   0.0
3       Pedestrian Plaza   0.0
4                   Park   0.0


----Annadale----
                   venue  freq
0      Accessories Store   0.0
1     Persian Restaurant   0.0
2  Performing Arts Venue   0.0
3       Pedestrian Plaza   0.0
4                   Park   0.0


----Arden Heights----
                   venue  freq
0      Accessories Store   0.0
1               Pet Café   0.0
2    Peruvian Restaurant   0.0
3     Persian Restaurant   0.0
4  Performing Arts Venue   0.0


----Arlington----
                 venue  freq
0    Accessories Store   0.0
1          Pet Service   0.0
2             Pet Café   0.0
3  Peruvian Restaurant   0.0
4   Persian Restaurant   0.0


----Arrochar----
                   venue  freq
0      Accessories Store   0.0
1               Pet Café   0.0
2    Peruvian Restaurant   0.0
3     Persian Restaurant   0.0
4  Performing 

## Finding top diffent venues in New York

In [95]:
def return_most_different_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=True)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [96]:
import numpy as np

In [97]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighbourhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most different Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most different Venue'.format(ind+1))

# create a new dataframe
newyork_venues_sorted = pd.DataFrame(columns=columns)
newyork_venues_sorted['Neighbourhood'] = newyork_grouped['Neighbourhood']

for ind in np.arange(newyork_grouped.shape[0]):
    newyork_venues_sorted.iloc[ind, 1:] = return_most_different_venues(newyork_grouped.iloc[ind, :], num_top_venues)

newyork_venues_sorted

Neighbourhood 1st Most different Venue  \
0                     Allerton        Accessories Store   
1                     Annadale        Accessories Store   
2                Arden Heights        Accessories Store   
3                    Arlington        Accessories Store   
4                     Arrochar        Accessories Store   
5                      Arverne        Accessories Store   
6                      Astoria        Accessories Store   
7              Astoria Heights        Accessories Store   
8                   Auburndale        Accessories Store   
9                   Bath Beach        Accessories Store   
10           Battery Park City        Accessories Store   
11                   Bay Ridge        Accessories Store   
12                 Bay Terrace                Jazz Club   
13                  Baychester        Accessories Store   
14                     Bayside        Accessories Store   
15                   Bayswater        Accessories Store   
16                Bedford Park        Accessories Store   
17          Bedford Stuyvesant        Accessories Store   
18                  Beechhurst        Accessories Store   
19                    Bellaire        Accessories Store   
20                Belle Harbor        Accessories Store   
21                   Bellerose        Accessories Store   
22                     Belmont        Accessories Store   
23                 Bensonhurst        Accessories Store   
24                Bergen Beach        Accessories Store   
25                  Blissville        Accessories Store   
26                  Bloomfield        Accessories Store   
27                 Boerum Hill        Accessories Store   
28                Borough Park        Accessories Store   
29                Breezy Point        Accessories Store   
30                   Briarwood        Accessories Store   
31              Brighton Beach        Accessories Store   
32               Broad Channel        Accessories Store   
33           Broadway Junction        Accessories Store   
34                   Bronxdale        Accessories Store   
35            Brooklyn Heights        Accessories Store   
36                  Brookville        Accessories Store   
37                 Brownsville        Accessories Store   
38                  Bulls Head        Accessories Store   
39                    Bushwick        Accessories Store   
40                Butler Manor        Accessories Store   
41             Cambria Heights        Accessories Store   
42                    Canarsie        Accessories Store   
43               Carnegie Hill        Accessories Store   
44             Carroll Gardens        Accessories Store   
45                 Castle Hill        Accessories Store   
46           Castleton Corners        Accessories Store   
47              Central Harlem        Accessories Store   
48                  Charleston        Accessories Store   
49                     Chelsea        Accessories Store   
50                   Chinatown        Accessories Store   
51                 City Island        Accessories Store   
52                   City Line        Accessories Store   
53                Civic Center        Accessories Store   
54           Claremont Village        Accessories Store   
55                Clason Point        Accessories Store   
56                     Clifton        Accessories Store   
57                     Clinton        Accessories Store   
58                Clinton Hill        Accessories Store   
59                  Co-op City                Jazz Club   
60                 Cobble Hill        Accessories Store   
61               College Point        Accessories Store   
62                     Concord        Accessories Store   
63                   Concourse        Accessories Store   
64           Concourse Village        Accessories Store   
65                Coney Island        Accessories Store   
66                      Corona        Accessories Store   
67   

In [98]:
len(newyork_venues_sorted['Neighbourhood'].unique())

301

In [99]:
newyork_venues_sorted.shape

(301, 11)

## Creating Foursquare Url for Toronto to find the locations

In [100]:
LIMIT = 100
radius = 500
url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
    CLIENT_ID, 
    CLIENT_SECRET, 
    VERSION, 
    toronto_latitude, 
    toronto_longitude, 
    radius, 
    LIMIT)
url # display URL

'https://api.foursquare.com/v2/venues/explore?&client_id=V4R2D1ZL5GMRDPXDVRCXRNEP5UFBXMP1WTNBI2RLNAQPPTGD&client_secret=O1BSCSZSQSYFY5WKSTOWCDDJRMV3EXEATF50DRCAGYZ0Y0XV&v=20190112&ll=43.653963,-79.387207&radius=500&limit=100'

Send the GET request and examine the resutls

In [101]:
newyork_results = requests.get(url).json()
newyork_results

{'meta': {'code': 200, 'requestId': '5c3a9471f594df0eaee7a906'},
 'response': {'groups': [{'items': [{'reasons': {'count': 0,
       'items': [{'reasonName': 'globalInteractionReason',
         'summary': 'This spot is popular',
         'type': 'general'}]},
      'referralId': 'e-0-5227bb01498e17bf485e6202-0',
      'venue': {'categories': [{'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/parks_outdoors/neighborhood_',
          'suffix': '.png'},
         'id': '4f2a25ac4b909258e854f55f',
         'name': 'Neighborhood',
         'pluralName': 'Neighborhoods',
         'primary': True,
         'shortName': 'Neighborhood'}],
       'id': '5227bb01498e17bf485e6202',
       'location': {'cc': 'CA',
        'city': 'Toronto',
        'country': 'Canada',
        'distance': 174,
        'formattedAddress': ['Toronto ON', 'Canada'],
        'labeledLatLngs': [{'label': 'display',
          'lat': 43.65323167517444,
          'lng': -79.38529600606677}],
        'lat': 43.6532

### Writing the function to extracts the category of the venue

In [102]:
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

#### cleaning the json and structure it into a *pandas* dataframe.

In [103]:
venues = newyork_results['response']['groups'][0]['items']
    
nearby_venues = json_normalize(venues) # flatten JSON

# filter columns
filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng']
nearby_venues =nearby_venues.loc[:, filtered_columns]

# filter the category for each row
nearby_venues['venue.categories'] = nearby_venues.apply(get_category_type, axis=1)

# clean columns
nearby_venues.columns = [col.split(".")[-1] for col in nearby_venues.columns]

nearby_venues.head()

name        categories        lat        lng
0          Downtown Toronto      Neighborhood  43.653232 -79.385296
1  Textile Museum of Canada        Art Museum  43.654396 -79.386500
2        Sansotei Ramen 三草亭  Ramen Restaurant  43.655157 -79.386501
3                   Japango  Sushi Restaurant  43.655268 -79.385165
4               Cafe Plenty              Café  43.654571 -79.389450

In [104]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighbourhood', 
                  'Neighbourhood Latitude', 
                  'Neighbourhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [105]:
toronto_venues = getNearbyVenues(names=tor_data['Neighbourhood'],
                                   latitudes=tor_data['Latitude'],
                                   longitudes=tor_data['Longitude']
                                  )

Malvern
Highland Creek,Rouge Hill,Port Union
Guildwood,Morningside,West Hill
Woburn
Cedarbrae
Scarborough Village
East Birchmount Park,Ionview,Kennedy Park
Clairlea,Golden Mile,Oakridge
Cliffcrest,Cliffside,Scarborough Village West
Birch Cliff,Cliffside West
Dorset Park,Scarborough Town Centre,Wexford Heights
Maryvale,Wexford
Agincourt
Clarks Corners,Sullivan,Tam O'Shanter
Agincourt North,L'Amoreaux East,Milliken,Steeles East
L'Amoreaux West,Steeles West
Upper Rouge
Hillcrest Village
Fairview,Henry Farm,Oriole
Bayview Village
Silver Hills,York Mills
Newtonbrook,Willowdale
Willowdale South
York Mills West
Willowdale West
Parkwoods
Don Mills North
Flemingdon Park,Don Mills South
Bathurst Manor,Downsview North,Wilson Heights
Northwood Park,York University
CFB Toronto,Downsview East
Downsview West
Downsview Central
Downsview Northwest
Victoria Village
Woodbine Gardens,Parkview Hill
Woodbine Heights
The Beaches
Leaside
Thorncliffe Park
East Toronto
The Danforth West,Riverdale
The Beaches We

In [106]:
toronto_venues.head()

Neighbourhood  Neighbourhood Latitude  \
0                               Malvern               43.806686   
1  Highland Creek,Rouge Hill,Port Union               43.784535   
2  Highland Creek,Rouge Hill,Port Union               43.784535   
3       Guildwood,Morningside,West Hill               43.763573   
4       Guildwood,Morningside,West Hill               43.763573   

   Neighbourhood Longitude                            Venue  Venue Latitude  \
0               -79.194353                          Wendy's       43.807448   
1               -79.160497            Royal Canadian Legion       43.782533   
2               -79.160497        Affordable Toronto Movers       43.787919   
3               -79.188711  Swiss Chalet Rotisserie & Grill       43.767697   
4               -79.188711                G & G Electronics       43.765309   

   Venue Longitude        Venue Category  
0       -79.199056  Fast Food Restaurant  
1       -79.163085                   Bar  
2       -79.162977         Moving Target  
3       -79.189914           Pizza Place  
4       -79.191537     Electronics Store

In [107]:
toronto_venues.shape

(2251, 7)

In [108]:
toronto_venues.groupby('Neighbourhood').count()

Neighbourhood Latitude  \
Neighbourhood                                                                
Adelaide,King,Richmond                                                 100   
Agincourt                                                                4   
Agincourt North,L'Amoreaux East,Milliken,Steele...                       2   
Albion Gardens,Beaumond Heights,Humbergate,Jame...                      10   
Alderwood,Long Branch                                                   10   
Bathurst Manor,Downsview North,Wilson Heights                           17   
Bayview Village                                                          4   
Bedford Park,Lawrence Manor East                                        25   
Berczy Park                                                             54   
Birch Cliff,Cliffside West                                               4   
Bloordale Gardens,Eringate,Markland Wood,Old Bu...                       6   
Brockton,Exhibition Place,Parkdale Village                              19   
Business Reply Mail Processing Centre 969 Eastern                       17   
CFB Toronto,Downsview East                                               4   
CN Tower,Bathurst Quay,Island airport,Harbourfr...                      14   
Cabbagetown,St. James Town                                              47   
Caledonia-Fairbanks                                                      6   
Canada Post Gateway Processing Centre                                   11   
Cedarbrae                                                                8   
Central Bay Street                                                      82   
Chinatown,Grange Park,Kensington Market                                100   
Christie                                                                15   
Church and Wellesley                                                    87   
Clairlea,Golden Mile,Oakridge                                           10   
Clarks Corners,Sullivan,Tam O'Shanter                                    9   
Cliffcrest,Cliffside,Scarborough Village West                            3   
Cloverdale,Islington,Martin Grove,Princess Gard...                       2   
Commerce Court,Victoria Hotel                                          100   
Davisville                                                              36   
Davisville North                                                        10   
Deer Park,Forest Hill SE,Rathnelly,South Hill,S...                      14   
Del Ray,Keelesdale,Mount Dennis,Silverthorn                              5   
Design Exchange,Toronto Dominion Centre                                100   
Don Mills North                                                          5   
Dorset Park,Scarborough Town Centre,Wexford Hei...                       7   
Dovercourt Village,Dufferin                                             19   
Downsview Central                                                        3   
Downsview Northwest                                                      5   
Downsview West                                                           4   
East Birchmount Park,Ionview,Kennedy Park                                6   
East Toronto                                                             2   
Emery,Humberlea                                                          1   
Fairview,Henry Farm,Oriole                                              62   
First Canadian Place,Underground city                                  100   
Flemingdon Park,Don Mills South                                         20   
Forest Hill North,Forest Hill West                                       4   
Glencairn                                                                4   
Guildwood,Morningside,West Hill                                          6   
Harbord,University of Toronto                                           34   
Harbourfront East,Toronto Islands,Union Station                        100

In [109]:
len(toronto_venues['Venue Category'].unique())

276

### One hot encoding for Normalizing the Data

In [110]:
# one hot encoding
toronto_onehot = pd.get_dummies(toronto_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
toronto_onehot['Neighbourhood'] = toronto_venues['Neighbourhood'] 

# move neighborhood column to the first column
fixed_columns = [toronto_onehot.columns[-1]] + list(toronto_onehot.columns[:-1])
toronto_onehot = toronto_onehot[fixed_columns]

toronto_onehot.head()

Neighbourhood  Accessories Store  Adult Boutique  \
0                               Malvern                  0               0   
1  Highland Creek,Rouge Hill,Port Union                  0               0   
2  Highland Creek,Rouge Hill,Port Union                  0               0   
3       Guildwood,Morningside,West Hill                  0               0   
4       Guildwood,Morningside,West Hill                  0               0   

   Afghan Restaurant  Airport  Airport Food Court  Airport Gate  \
0                  0        0                   0             0   
1                  0        0                   0             0   
2                  0        0                   0             0   
3                  0        0                   0             0   
4                  0        0                   0             0   

   Airport Lounge  Airport Service  Airport Terminal  American Restaurant  \
0               0                0                 0                    0   
1               0                0                 0                    0   
2               0                0                 0                    0   
3               0                0                 0                    0   
4               0                0                 0                    0   

   Antique Shop  Aquarium  Arepa Restaurant  Art Gallery  Art Museum  \
0             0         0                 0            0           0   
1             0         0                 0            0           0   
2             0         0                 0            0           0   
3             0         0                 0            0           0   
4             0         0                 0            0           0   

   Arts & Crafts Store  Asian Restaurant  Athletics & Sports  Auto Garage  \
0                    0                 0                   0            0   
1                    0                 0                   0            0   
2                    0                 0                   0            0   
3                    0                 0                   0            0   
4                    0                 0                   0            0   

   Auto Workshop  BBQ Joint  Baby Store  Bagel Shop  Bakery  Bank  Bar  \
0              0          0           0           0       0     0    0   
1              0          0           0           0       0     0    1   
2              0          0           0           0       0     0    0   
3              0          0           0           0       0     0    0   
4              0          0           0           0       0     0    0   

   Baseball Field  Baseball Stadium  Basketball Court  Basketball Stadium  \
0               0                 0                 0                   0   
1               0                 0                 0                   0   
2               0                 0                 0                   0   
3               0                 0                 0                   0   
4               0                 0                 0                   0   

   Beach  Beer Bar  Beer Store  Belgian Restaurant  Bike Shop  Bistro  \
0      0         0           0                   0          0       0   
1      0         0           0                   0          0       0   
2      0         0           0                   0          0       0   
3      0         0           0                   0          0       0   
4      0         0           0                   0          0       0   

   Board Shop  Boat or Ferry  Bookstore  Boutique  Brazilian Restaurant  \
0           0              0          0         0                     0   
1           0              0          0         0                     0   
2           0              0          0         0                     0   
3           0              0          0         0                     0   
4           0              0          0         0                     0  

In [111]:
toronto_grouped = toronto_onehot.groupby('Neighbourhood').mean().reset_index()
toronto_grouped

Neighbourhood  Accessories Store  \
0                              Adelaide,King,Richmond           0.000000   
1                                           Agincourt           0.000000   
2   Agincourt North,L'Amoreaux East,Milliken,Steel...           0.000000   
3   Albion Gardens,Beaumond Heights,Humbergate,Jam...           0.000000   
4                               Alderwood,Long Branch           0.000000   
5       Bathurst Manor,Downsview North,Wilson Heights           0.000000   
6                                     Bayview Village           0.000000   
7                    Bedford Park,Lawrence Manor East           0.000000   
8                                         Berczy Park           0.000000   
9                          Birch Cliff,Cliffside West           0.000000   
10  Bloordale Gardens,Eringate,Markland Wood,Old B...           0.000000   
11         Brockton,Exhibition Place,Parkdale Village           0.000000   
12  Business Reply Mail Processing Centre 969 Eastern           0.000000   
13                         CFB Toronto,Downsview East           0.000000   
14  CN Tower,Bathurst Quay,Island airport,Harbourf...           0.000000   
15                         Cabbagetown,St. James Town           0.000000   
16                                Caledonia-Fairbanks           0.000000   
17              Canada Post Gateway Processing Centre           0.000000   
18                                          Cedarbrae           0.000000   
19                                 Central Bay Street           0.000000   
20            Chinatown,Grange Park,Kensington Market           0.000000   
21                                           Christie           0.000000   
22                               Church and Wellesley           0.000000   
23                      Clairlea,Golden Mile,Oakridge           0.000000   
24              Clarks Corners,Sullivan,Tam O'Shanter           0.000000   
25      Cliffcrest,Cliffside,Scarborough Village West           0.000000   
26  Cloverdale,Islington,Martin Grove,Princess Gar...           0.000000   
27                      Commerce Court,Victoria Hotel           0.000000   
28                                         Davisville           0.000000   
29                                   Davisville North           0.000000   
30  Deer Park,Forest Hill SE,Rathnelly,South Hill,...           0.000000   
31        Del Ray,Keelesdale,Mount Dennis,Silverthorn           0.000000   
32            Design Exchange,Toronto Dominion Centre           0.000000   
33                                    Don Mills North           0.000000   
34  Dorset Park,Scarborough Town Centre,Wexford He...           0.000000   
35                        Dovercourt Village,Dufferin           0.000000   
36                                  Downsview Central           0.000000   
37                                Downsview Northwest           0.000000   
38                                     Downsview West           0.000000   
39          East Birchmount Park,Ionview,Kennedy Park           0.000000   
40                                       East Toronto           0.000000   
41                                    Emery,Humberlea           0.000000   
42                         Fairview,Henry Farm,Oriole           0.000000   
43              First Canadian Place,Underground city           0.000000   
44                    Flemingdon Park,Don Mills South           0.000000   
45                 Forest Hill North,Forest Hill West           0.000000   
46                                          Glencairn           0.000000   
47                    Guildwood,Morningside,West Hill           0.000000   
48                      Harbord,University of Toronto           0.000000   
49    Harbourfront East,Toronto Islands,Union Station           0.000000   
50                           Harbourfront,Regent Park           0.000000   
51                       High Park,The Junction South           0.000000   
52          

### Finding the Frequencies of Neighbourhoods for Toronto

In [112]:
num_top_venues = 5

for hood in toronto_grouped['Neighbourhood']:
    print("----"+hood+"----")
    temp = toronto_grouped[toronto_grouped['Neighbourhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=True).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Adelaide,King,Richmond----
                       venue  freq
0          Accessories Store   0.0
1  Latin American Restaurant   0.0
2         Light Rail Station   0.0
3             Lingerie Store   0.0
4               Liquor Store   0.0


----Agincourt----
                      venue  freq
0         Accessories Store   0.0
1            Massage Studio   0.0
2            Medical Center   0.0
3  Mediterranean Restaurant   0.0
4               Men's Store   0.0


----Agincourt North,L'Amoreaux East,Milliken,Steeles East----
                      venue  freq
0         Accessories Store   0.0
1            Massage Studio   0.0
2            Medical Center   0.0
3  Mediterranean Restaurant   0.0
4               Men's Store   0.0


----Albion Gardens,Beaumond Heights,Humbergate,Jamestown,Mount Olive,Silverstone,South Steeles,Thistletown----
                      venue  freq
0         Accessories Store   0.0
1            Massage Studio   0.0
2            Medical Center   0.0
3  Mediterranean R

## Finding top diffent venues in Toronto

In [113]:
def return_most_different_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=True)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [114]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighbourhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most different Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most different Venue'.format(ind+1))

# create a new dataframe
toronto_venues_sorted = pd.DataFrame(columns=columns)
toronto_venues_sorted['Neighbourhood'] = toronto_grouped['Neighbourhood']

for ind in np.arange(toronto_grouped.shape[0]):
    toronto_venues_sorted.iloc[ind, 1:] = return_most_different_venues(toronto_grouped.iloc[ind, :], num_top_venues)

toronto_venues_sorted

Neighbourhood  \
0                              Adelaide,King,Richmond   
1                                           Agincourt   
2   Agincourt North,L'Amoreaux East,Milliken,Steel...   
3   Albion Gardens,Beaumond Heights,Humbergate,Jam...   
4                               Alderwood,Long Branch   
5       Bathurst Manor,Downsview North,Wilson Heights   
6                                     Bayview Village   
7                    Bedford Park,Lawrence Manor East   
8                                         Berczy Park   
9                          Birch Cliff,Cliffside West   
10  Bloordale Gardens,Eringate,Markland Wood,Old B...   
11         Brockton,Exhibition Place,Parkdale Village   
12  Business Reply Mail Processing Centre 969 Eastern   
13                         CFB Toronto,Downsview East   
14  CN Tower,Bathurst Quay,Island airport,Harbourf...   
15                         Cabbagetown,St. James Town   
16                                Caledonia-Fairbanks   
17              Canada Post Gateway Processing Centre   
18                                          Cedarbrae   
19                                 Central Bay Street   
20            Chinatown,Grange Park,Kensington Market   
21                                           Christie   
22                               Church and Wellesley   
23                      Clairlea,Golden Mile,Oakridge   
24              Clarks Corners,Sullivan,Tam O'Shanter   
25      Cliffcrest,Cliffside,Scarborough Village West   
26  Cloverdale,Islington,Martin Grove,Princess Gar...   
27                      Commerce Court,Victoria Hotel   
28                                         Davisville   
29                                   Davisville North   
30  Deer Park,Forest Hill SE,Rathnelly,South Hill,...   
31        Del Ray,Keelesdale,Mount Dennis,Silverthorn   
32            Design Exchange,Toronto Dominion Centre   
33                                    Don Mills North   
34  Dorset Park,Scarborough Town Centre,Wexford He...   
35                        Dovercourt Village,Dufferin   
36                                  Downsview Central   
37                                Downsview Northwest   
38                                     Downsview West   
39          East Birchmount Park,Ionview,Kennedy Park   
40                                       East Toronto   
41                                    Emery,Humberlea   
42                         Fairview,Henry Farm,Oriole   
43              First Canadian Place,Underground city   
44                    Flemingdon Park,Don Mills South   
45                 Forest Hill North,Forest Hill West   
46                                          Glencairn   
47                    Guildwood,Morningside,West Hill   
48                      Harbord,University of Toronto   
49    Harbourfront East,Toronto Islands,Union Station   
50                           Harbourfront,Regent Park   
51                       High Park,The Junction South   
52               Highland Creek,Rouge Hill,Port Union   
53                                  Hillcrest Village   
54         Humber Bay Shores,Mimico South,New Toronto   
55  Humber Bay,King's Mill Park,Kingsway Park Sout...   
56                                      Humber Summit   
57                                 Humewood-Cedarvale   
58  Kingsview Village,Martin Grove Gardens,Richvie...   
59  Kingsway Park South West,Mimico NW,The Queensw...   
60                       L'Amoreaux West,Steeles West   
61                    Lawrence Heights,Lawrence Manor   
62                                      Lawrence Park   
63                                            Leaside   
64                            Little Portugal,Trinity   
65                                            Malvern   
66             Maple Leaf Park,North Park,Upwood Park   
67                                   Maryvale,Wexford   
68                         Moore Park,Summerhill East   
69                                 North Toronto W

In [115]:
print("Toronto neighbourhood values :",toronto_venues_sorted.shape)
print("New York neighbourhood Values :",newyork_venues_sorted.shape)

Toronto neighbourhood values : (99, 11)
New York neighbourhood Values : (301, 11)


## Now we are using the Clustering algorithm on Two Cities <br>
Finding the each and every borough's neighbourhoods

In [116]:
# import k-means from clustering stage
from sklearn.cluster import KMeans

In [117]:
# set number of clusters
kclusters = 5

newyork_grouped_clustering = newyork_grouped.drop('Neighbourhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(newyork_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([0, 0, 3, 3, 3, 0, 0, 0, 0, 0], dtype=int32)

In [118]:
newyorkdata.shape

(302, 4)

In [119]:
newyork_venues_sorted.shape

(301, 11)

#### Finding the non matching rows in two data frames 

In [120]:
dff=pd.concat([newyorkdata['Neighbourhood'],newyork_venues_sorted['Neighbourhood']])
dff=dff.reset_index(drop=True)
df_grp=dff.groupby(list(dff.values))
idx=[x[0] for x in df_grp.groups.values() if len(x)==1]
dff.reindex(idx)

253    Howland Hook
Name: Neighbourhood, dtype: object

In [121]:
newyorkdata['Neighbourhood']=='Howland Hook'

0      False
1      False
2      False
3      False
4      False
5      False
6      False
7      False
8      False
9      False
10     False
11     False
12     False
13     False
14     False
15     False
16     False
17     False
18     False
19     False
20     False
21     False
22     False
23     False
24     False
25     False
26     False
27     False
28     False
29     False
30     False
31     False
32     False
33     False
34     False
35     False
36     False
37     False
38     False
39     False
40     False
41     False
42     False
43     False
44     False
45     False
46     False
47     False
48     False
49     False
50     False
51     False
52     False
53     False
54     False
55     False
56     False
57     False
58     False
59     False
60     False
61     False
62     False
63     False
64     False
65     False
66     False
67     False
68     False
69     False
70     False
71     False
72     False
73     False
74     False
75     False
76     False

In [122]:
newyorkdata=newyorkdata.drop(newyorkdata.index[257])

In [123]:
newyorkdata.shape

(301, 4)

Let's create a new dataframe that includes the cluster as well as the top 10 venues for each neighborhood.

In [124]:
newyork_merged = newyorkdata

# add clustering labels
newyork_merged['Cluster Labels'] = kmeans.labels_

# merge newyork_grouped with newyork_data to add latitude/longitude for each neighborhood
newyork_merged = newyork_merged.join(newyork_venues_sorted.set_index('Neighbourhood'), on='Neighbourhood')

newyork_merged.head() # check the last columns!

Borough Neighbourhood   Latitude  Longitude  Cluster Labels  \
0   Bronx     Wakefield  40.894705 -73.847201               0   
1   Bronx    Co-op City  40.874294 -73.829939               0   
2   Bronx   Eastchester  40.887556 -73.827806               3   
3   Bronx     Fieldston  40.895437 -73.905643               3   
4   Bronx     Riverdale  40.890834 -73.912585               3   

  1st Most different Venue 2nd Most different Venue 3rd Most different Venue  \
0        Accessories Store      Peruvian Restaurant       Persian Restaurant   
1                Jazz Club      Peruvian Restaurant       Persian Restaurant   
2        Accessories Store                 Pet Café      Peruvian Restaurant   
3        Accessories Store      Peruvian Restaurant       Persian Restaurant   
4        Accessories Store                 Pet Café      Peruvian Restaurant   

  4th Most different Venue 5th Most different Venue 6th Most different Venue  \
0    Performing Arts Venue         Pedestrian Plaza                     Park   
1    Performing Arts Venue         Pedestrian Plaza                     Park   
2       Persian Restaurant    Performing Arts Venue         Pedestrian Plaza   
3    Performing Arts Venue         Pedestrian Plaza                     Park   
4       Persian Restaurant    Performing Arts Venue         Pedestrian Plaza   

        7th Most different Venue       8th Most different Venue  \
0  Paper / Office Supplies Store           Pakistani Restaurant   
1  Paper / Office Supplies Store           Pakistani Restaurant   
2                           Park  Paper / Office Supplies Store   
3  Paper / Office Supplies Store           Pakistani Restaurant   
4  Paper / Office Supplies Store           Pakistani Restaurant   

  9th Most different Venue 10th Most different Venue  
0        Paella Restaurant              Outlet Store  
1        Paella Restaurant              Outlet Store  
2     Pakistani Restaurant         Paella Restaurant  
3        Paella Restaurant              Outlet Store  
4        Paella Restaurant              Outlet Store

In [125]:
import matplotlib.cm as cm
import matplotlib.colors as colors

In [126]:
# create map
map_clusters = folium.Map(location=[newyork_latitude, newyork_longitude], zoom_start=10)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i+x+(i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(newyork_merged['Latitude'], newyork_merged['Longitude'], newyork_merged['Neighbourhood'], newyork_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

## Toronto - clustering

In [127]:
# set number of clusters
kclusters = 5

toronto_grouped_clustering = toronto_grouped.drop('Neighbourhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(toronto_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([1, 1, 4, 1, 1, 1, 1, 1, 1, 1], dtype=int32)

In [128]:
len(tor_data['Neighbourhood'].unique())

103

In [129]:
len(toronto_venues_sorted['Neighbourhood'].unique())

99

#### Drop Non matching rows in two Data frames 

In [130]:
tor_data[~tor_data.index.isin(toronto_venues_sorted.index)]

Borough                                      Neighbourhood   Latitude  \
99   Etobicoke                                          Westmount  43.696319   
100  Etobicoke  Kingsview Village,Martin Grove Gardens,Richvie...  43.688905   
101  Etobicoke  Albion Gardens,Beaumond Heights,Humbergate,Jam...  43.739416   
102  Etobicoke                                          Northwest  43.706748   

     Longitude  
99  -79.532242  
100 -79.554724  
101 -79.588437  
102 -79.594054

In [131]:
tor_data=tor_data.drop(tor_data.index[[99,100,101,102]])

In [132]:
tor_data.shape

(99, 4)

In [133]:
toronto_merged = tor_data

# add clustering labels
toronto_merged['Cluster Labels'] = kmeans.labels_

# merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
toronto_merged = toronto_merged.join(toronto_venues_sorted.set_index('Neighbourhood'), on='Neighbourhood')

toronto_merged.head() # check the last columns!

Borough                         Neighbourhood   Latitude  Longitude  \
0  Scarborough                               Malvern  43.806686 -79.194353   
1  Scarborough  Highland Creek,Rouge Hill,Port Union  43.784535 -79.160497   
2  Scarborough       Guildwood,Morningside,West Hill  43.763573 -79.188711   
3  Scarborough                                Woburn  43.770992 -79.216917   
4  Scarborough                             Cedarbrae  43.773136 -79.239476   

   Cluster Labels 1st Most different Venue  2nd Most different Venue  \
0               1        Accessories Store  Mediterranean Restaurant   
1               1        Accessories Store            Medical Center   
2               4        Accessories Store         Martial Arts Dojo   
3               1        Accessories Store            Medical Center   
4               1        Accessories Store            Medical Center   

   3rd Most different Venue  4th Most different Venue  \
0               Men's Store             Metro Station   
1  Mediterranean Restaurant               Men's Store   
2            Massage Studio  Mediterranean Restaurant   
3  Mediterranean Restaurant               Men's Store   
4  Mediterranean Restaurant               Men's Store   

  5th Most different Venue   6th Most different Venue  \
0       Mexican Restaurant  Middle Eastern Restaurant   
1            Metro Station         Mexican Restaurant   
2              Men's Store              Metro Station   
3            Metro Station         Mexican Restaurant   
4            Metro Station         Mexican Restaurant   

    7th Most different Venue 8th Most different Venue  \
0         Miscellaneous Shop        Mobile Phone Shop   
1  Middle Eastern Restaurant       Miscellaneous Shop   
2  Middle Eastern Restaurant       Miscellaneous Shop   
3  Middle Eastern Restaurant       Miscellaneous Shop   
4  Middle Eastern Restaurant       Miscellaneous Shop   

     9th Most different Venue        10th Most different Venue  
0  Modern European Restaurant  Molecular Gastronomy Restaurant  
1           Mobile Phone Shop       Modern European Restaurant  
2           Mobile Phone Shop       Modern European Restaurant  
3           Mobile Phone Shop       Modern European Restaurant  
4           Mobile Phone Shop       Modern European Restaurant

In [134]:
# create map
map_clusters = folium.Map(location=[toronto_latitude, toronto_longitude], zoom_start=10)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i+x+(i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(toronto_merged['Latitude'], toronto_merged['Longitude'], toronto_merged['Neighbourhood'], toronto_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

## Finalize the Result

Here are Two cities of New York and Toronto, which are top most non matching stores along with <b>"Neighbourhoods"</b>

In [135]:
newyork_merged.head()

Borough Neighbourhood   Latitude  Longitude  Cluster Labels  \
0   Bronx     Wakefield  40.894705 -73.847201               0   
1   Bronx    Co-op City  40.874294 -73.829939               0   
2   Bronx   Eastchester  40.887556 -73.827806               3   
3   Bronx     Fieldston  40.895437 -73.905643               3   
4   Bronx     Riverdale  40.890834 -73.912585               3   

  1st Most different Venue 2nd Most different Venue 3rd Most different Venue  \
0        Accessories Store      Peruvian Restaurant       Persian Restaurant   
1                Jazz Club      Peruvian Restaurant       Persian Restaurant   
2        Accessories Store                 Pet Café      Peruvian Restaurant   
3        Accessories Store      Peruvian Restaurant       Persian Restaurant   
4        Accessories Store                 Pet Café      Peruvian Restaurant   

  4th Most different Venue 5th Most different Venue 6th Most different Venue  \
0    Performing Arts Venue         Pedestrian Plaza                     Park   
1    Performing Arts Venue         Pedestrian Plaza                     Park   
2       Persian Restaurant    Performing Arts Venue         Pedestrian Plaza   
3    Performing Arts Venue         Pedestrian Plaza                     Park   
4       Persian Restaurant    Performing Arts Venue         Pedestrian Plaza   

        7th Most different Venue       8th Most different Venue  \
0  Paper / Office Supplies Store           Pakistani Restaurant   
1  Paper / Office Supplies Store           Pakistani Restaurant   
2                           Park  Paper / Office Supplies Store   
3  Paper / Office Supplies Store           Pakistani Restaurant   
4  Paper / Office Supplies Store           Pakistani Restaurant   

  9th Most different Venue 10th Most different Venue  
0        Paella Restaurant              Outlet Store  
1        Paella Restaurant              Outlet Store  
2     Pakistani Restaurant         Paella Restaurant  
3        Paella Restaurant              Outlet Store  
4        Paella Restaurant              Outlet Store

In [136]:
toronto_merged.head()

Borough                         Neighbourhood   Latitude  Longitude  \
0  Scarborough                               Malvern  43.806686 -79.194353   
1  Scarborough  Highland Creek,Rouge Hill,Port Union  43.784535 -79.160497   
2  Scarborough       Guildwood,Morningside,West Hill  43.763573 -79.188711   
3  Scarborough                                Woburn  43.770992 -79.216917   
4  Scarborough                             Cedarbrae  43.773136 -79.239476   

   Cluster Labels 1st Most different Venue  2nd Most different Venue  \
0               1        Accessories Store  Mediterranean Restaurant   
1               1        Accessories Store            Medical Center   
2               4        Accessories Store         Martial Arts Dojo   
3               1        Accessories Store            Medical Center   
4               1        Accessories Store            Medical Center   

   3rd Most different Venue  4th Most different Venue  \
0               Men's Store             Metro Station   
1  Mediterranean Restaurant               Men's Store   
2            Massage Studio  Mediterranean Restaurant   
3  Mediterranean Restaurant               Men's Store   
4  Mediterranean Restaurant               Men's Store   

  5th Most different Venue   6th Most different Venue  \
0       Mexican Restaurant  Middle Eastern Restaurant   
1            Metro Station         Mexican Restaurant   
2              Men's Store              Metro Station   
3            Metro Station         Mexican Restaurant   
4            Metro Station         Mexican Restaurant   

    7th Most different Venue 8th Most different Venue  \
0         Miscellaneous Shop        Mobile Phone Shop   
1  Middle Eastern Restaurant       Miscellaneous Shop   
2  Middle Eastern Restaurant       Miscellaneous Shop   
3  Middle Eastern Restaurant       Miscellaneous Shop   
4  Middle Eastern Restaurant       Miscellaneous Shop   

     9th Most different Venue        10th Most different Venue  
0  Modern European Restaurant  Molecular Gastronomy Restaurant  
1           Mobile Phone Shop       Modern European Restaurant  
2           Mobile Phone Shop       Modern European Restaurant  
3           Mobile Phone Shop       Modern European Restaurant  
4           Mobile Phone Shop       Modern European Restaurant

By comparing above two Cities <br>

Best recommand is in Toronto city and New York, Choices to open a store "Accessories Store"
we have different type of restaurents in that best recommand restaurents are<br>
### Peruvian,Persian,Pakistani,paella Restaurents (To open in the place <b>"Bronx"</b> of New York city)<br>
### Mediterranean,Mexican,Middle Estern,Modern European Restaurents (To open in the place <b>"Scarborough"</b> of Toronto city)



We can able to choose many stores like this....

# <center>...Thank You...</center>